In [1]:
import folium

In [2]:
%run '../scripts/ETL.py' '../scripts/paths.json'

/Users/Kasturi/opt/anaconda3/lib/python3.9/site-packages/geopandas/_compat.py:112: UserWarning: The Shapely GEOS version (3.10.2-CAPI-1.16.0) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


22/10/07 13:09:58 WARN Utils: Your hostname, MacBook-Air-3.local resolves to a loopback address: 127.0.0.1; using 192.168.0.66 instead (on interface en0)
22/10/07 13:09:58 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


22/10/07 13:09:59 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
22/10/07 13:09:59 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


22/10/07 13:11:09 WARN package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


In [3]:
final_join3.limit(5)

+--------------------+------------+--------------------+---------+--------------+--------------------+--------------------+-----+------+------------------+------------------+--------------------+--------------+-------+-----------+-------+---------+----------+----------+---------+---------+-------------------+----------------+-----------+-------------+-------------+----------+---------------+---------------+---------------+--------------------------+--------------------------+
|       merchant_name|merchant_abn|          categories|take_rate|revenue_levels|                name|             address|state|gender|trans_merchant_abn|      dollar_value|            order_id|order_datetime|user_id|consumer_id| suburb|postcodes|      long|       lat|  int_sa2| SA2_code|           SA2_name|income_2018-2019|total_males|total_females|total_persons|state_code|     state_name|population_2020|population_2021|fraud_probability_consumer|fraud_probability_merchant|
+--------------------+------------+--------------------+---------+--------------+--------------------+--------------------+-----+------+------------------+------------------+--------------------+--------------+-------+-----------+-------+---------+----------+----------+---------+---------+-------------------+----------------+-----------+-------------+-------------+----------+---------------+---------------+---------------+--------------------------+--------------------------+
|Egestas Nunc Asso...| 11121775571|digital goods: bo...|     6.58|             a|Christopher Rodri...|30554 Evans Strea...|  NSW|  Male|       11121775571| 11.28829564583802|2bd2a61d-72e5-42d...|    2021-08-20|   3698|       1175|JESMOND|     2299|151.704581|-32.909816|111031231|111031231|Shortland - Jesmond|       242936885|       6412|         6179|        12593|         1|New South Wales|          12598|          12694|                      0.01|                      0.01|
|Morbi Accumsan In...| 19618998054|tent and aWning s...|     1.52|             c|Christopher Rodri...|30554 Evans Strea...|  NSW|  Male|       19618998054| 62.90176609196828|3582b1f8-4577-403...|    2021-05-16|   3698|       1175|JESMOND|     2299|151.704581|-32.909816|111031231|111031231|Shortland - Jesmond|       242936885|       6412|         6179|        12593|         1|New South Wales|          12598|          12694|                      0.01|                      0.01|
| Eu Dolor Egestas PC| 94472466107|cable, satellite,...|     6.23|             a|Christopher Rodri...|30554 Evans Strea...|  NSW|  Male|       94472466107|172.15375126873164|cb05d49f-c2fa-453...|    2021-07-22|   3698|       1175|JESMOND|     2299|151.704581|-32.909816|111031231|111031231|Shortland - Jesmond|       242936885|       6412|         6179|        12593|         1|New South Wales|          12598|          12694|                      0.01|                      0.01|
|Urna Justo Indust...| 31472801314|music shops - mus...|     6.56|             a|Christopher Rodri...|30554 Evans Strea...|  NSW|  Male|       31472801314|0.4894787650356477|aeec15c1-67e8-4cb...|    2021-05-18|   3698|       1175|JESMOND|     2299|151.704581|-32.909816|111031231|111031231|Shortland - Jesmond|       242936885|       6412|         6179|        12593|         1|New South Wales|          12598|          12694|                      0.01|                      0.01|
|Eu Sem Pellentesq...| 35424691626|computers, comput...|      3.9|             b|Christopher Rodri...|30554 Evans Strea...|  NSW|  Male|       35424691626| 7.360217018778133|9df473ba-102d-461...|    2021-07-04|   3698|       1175|JESMOND|     2299|151.704581|-32.909816|111031231|111031231|Shortland - Jesmond|       242936885|       6412|         6179|        12593|         1|New South Wales|          12598|          12694|                      0.01|                      0.01|
+--------------------+------------+--------------------+---------+--------------+--------------------+--------------------+-----+------+----------------

In [4]:
final_join3.select("postcodes").distinct().count()

2343

In [5]:
num_transactions_by_postcode = final_join3.groupBy(['postcodes', 'suburb', 'long', 'lat']).count()

In [6]:
# conver transactions location to pandas df
num_transactions_by_postcode_pdf = num_transactions_by_postcode.toPandas()

aus_coords = [-25.2744, 133.7751]
m = folium.Map(aus_coords, tiles='OpenStreetMap', zoom_start=4.5)

for index, row in num_transactions_by_postcode_pdf.iterrows():
    if row['count'] >= 10000:
        marker_color = 'darkred'
        fill_color = 'darkred'
    elif row['count'] >= 5000:
        marker_color = 'red'
        fill_color = 'red'
    elif row['count'] >= 500:
        marker_color = 'darkorange'
        fill_color = 'darkorange'
    elif row['count'] >= 100:
        marker_color = 'orange'
        fill_color = 'orange'
    elif row['count'] <= 50 :
        marker_color = 'yellow'
        fill_color = 'yellow'
    else:
        marker_color='darkpurple'
        fill_color = 'darkpurple'
        
    folium.Circle(
          location=[row['lat'], row['long']],
          popup= 'Number of transactions: ' +str(row['count']),
          tooltip=row['suburb'],
          radius=row['count'],
          color=marker_color,
          fill=True,
          fill_color=fill_color,
       ).add_to(m)
m.save('../plots/bubble_plot_num_transactions_by_location.html')

In [8]:
m

In [7]:
%run '../scripts/fraud_feature.py' '../scripts/paths.json'

Exception: File `'../scripts/fraud_feature.py'` not found.

In [ ]:

fraud_by_postcode = pd.read_parquet('../data/tables/full_dataset_with_fraud_rates.parquet')
fraud_by_postcode.head(5)

merchant_name  merchant_abn categories  take_rate revenue_levels  \
0          None           NaN       None        NaN           None   
1          None           NaN       None        NaN           None   
2          None           NaN       None        NaN           None   
3          None           NaN       None        NaN           None   
4          None           NaN       None        NaN           None   

                  name                        address state postcode  \
0            Jose Frye    394 Matthews View Suite 660   NSW     2021   
1  Mrs. Valerie Powell   23459 Nicole Green Suite 420   VIC     3194   
2         Maria Miller    3893 Martin Knoll Suite 887   NSW     2038   
3    Alexander Skinner  35694 Kimberly Coves Apt. 057   VIC     3053   
4    Alexander Skinner  35694 Kimberly Coves Apt. 057   VIC     3053   

        gender  trans_merchant_abn  dollar_value  \
0         Male        8.078817e+10     86.718630   
1       Female        8.078817e+10      1.572543   
2  Undisclosed        8.078817e+10     48.925310   
3         Male        8.078817e+10    168.737463   
4         Male        8.078817e+10    127.266580   

                               order_id order_datetime  user_id  consumer_id  \
0  1c60001e-77cd-4755-9a89-265b4f197dc5     2021-04-21   5156.0      19115.0   
1  459f4f62-3953-4318-8de1-4b0bbc673cf1     2021-07-07   8323.0      69735.0   
2  25d0ea41-da85-4930-aa25-7abedad2da8a     2021-03-25   3635.0      72910.0   
3  1a5ffb5a-2d40-4127-8377-7e82409712f1     2021-12-30   9248.0     147322.0   
4  8bddc10d-14a4-4c8f-a904-ed03b76008d6     2021-09-21   9248.0     147322.0   

   sus_merchant_abn  average fraud rate per merchant  
0               NaN                              NaN  
1               NaN                              NaN  
2               NaN                              NaN  
3               NaN                              NaN  
4               NaN                              NaN